# Fatima Fellowship Quick Coding Challenge (Pick 1)

Thank you for applying to the Fatima Fellowship. To help us select the Fellows and assess your ability to do machine learning research, we are asking that you complete a short coding challenge. Please pick **1 of these 5** coding challenges, whichever is most aligned with your interests. 

**Due date: 1 week**

**How to submit**: Please make a copy of this colab notebook, add your code and results, and submit your colab notebook to the submission link below. If you have never used a colab notebook, [check out this video](https://www.youtube.com/watch?v=i-HnvsehuSw).

**Submission link**: https://airtable.com/shrXy3QKSsO2yALd3

# 1. Deep Learning for Vision

**Upside down detector**: Train a model to detect if images are upside down

* Pick a dataset of natural images (we suggest looking at datasets on the [Hugging Face Hub](https://huggingface.co/datasets?task_categories=task_categories:image-classification&sort=downloads))
* Synthetically turn some of images upside down. Create a training and test set.
* Build a neural network (using Tensorflow, PyTorch, or any framework you like)
* Train it to classify image orientation until a reasonable accuracy is reached
* [Upload the the model to the Hugging Face Hub](https://huggingface.co/docs/hub/adding-a-model), and add a link to your model below.
* Look at some of the images that were classified incorrectly. Please explain what you might do to improve your model's performance on these images in the future (you do not need to impelement these suggestions)

**Submission instructions**: Please write your code below and include some examples of images that were classified

# 2. Deep Learning for NLP

**Fake news classifier**: Train a text classification model to detect fake news articles!

* Download the dataset here: https://www.kaggle.com/clmentbisaillon/fake-and-real-news-dataset
* Develop an NLP model for classification that uses a pretrained language model
* Finetune your model on the dataset, and generate an AUC curve of your model on the test set of your choice. 
* [Upload the the model to the Hugging Face Hub](https://huggingface.co/docs/hub/adding-a-model), and add a link to your model below.
* *Answer the following question*: Look at some of the news articles that were classified incorrectly. Please explain what you might do to improve your model's performance on these news articles in the future (you do not need to impelement these suggestions)

In [ ]:
### WRITE YOUR CODE TO TRAIN THE MODEL HERE

Connecting to drive

In [1]:
from google.colab import drive
drive.mount('/root/gdrive', force_remount=True)

Mounted at /root/gdrive


Going To Root directory where the dataset is stored

In [2]:
%cd /root/gdrive/MyDrive/Fake news detection

/root/gdrive/MyDrive/Fake news detection


In [3]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

Data preprocessing

In [4]:
fake=pd.read_csv('Fake.csv')
true=pd.read_csv('True.csv')
print(fake.shape, true.shape)

(23481, 4) (21417, 4)


In [5]:
fake.drop(['date', 'subject'], axis=1, inplace=True)
true.drop(['date', 'subject'], axis=1, inplace=True)
fake['class'] = 0 
true['class'] = 1
print(fake.shape, true.shape)

(23481, 3) (21417, 3)


In [6]:
fake['text'] = fake['title'] + fake['text']
true['text'] = true['title'] + true['text']
fake.drop('title', axis=1, inplace=True)
true.drop('title', axis=1, inplace=True)
print(fake.shape, true.shape)

(23481, 2) (21417, 2)


In [7]:
data = pd.concat([fake, true], ignore_index=True, sort=False).sample(frac=1)
print(data.shape,data.head())

(44898, 2)                                                     text  class
30805  A discontented Michigan town: America should h...      1
41251  Iran president defends Guards in show of unity...      1
3629    White Man Dedicates His Racist Attack To Trum...      0
24764  Trump healthcare order could run afoul of reti...      1
23861  How McConnell kept Republicans in line to win ...      1


Working for only 2000 data because of google colab RAM and disk issue

In [8]:
data = data[:2000]

In [9]:
x_text = data['text'].values.tolist()
y_label = data['class'].values.tolist()
print(np.shape(x_text), type(x_text))

(2000,) <class 'list'>


Splitting into train-test set

In [10]:
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(x_text,y_label, stratify=y_label)

In [11]:
import tensorflow as tf
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.callbacks import EarlyStopping
from tensorflow.keras.initializers import TruncatedNormal
from tensorflow.keras.losses import CategoricalCrossentropy
from tensorflow.keras.metrics import CategoricalAccuracy
from tensorflow.keras.utils import to_categorical
from tensorflow.keras.layers import Input, Dense

Library installing for XLMRoBERTa model

In [12]:
!pip install transformers
import transformers

     |████████████████████████████████| 3.8 MB 5.0 MB/s 
     |████████████████████████████████| 895 kB 45.7 MB/s 
     |████████████████████████████████| 6.5 MB 30.8 MB/s 
     |████████████████████████████████| 67 kB 4.9 MB/s 
     |████████████████████████████████| 596 kB 46.4 MB/s 
  Attempting uninstall: pyyaml
    Found existing installation: PyYAML 3.13
    Uninstalling PyYAML-3.13:
      Successfully uninstalled PyYAML-3.13


In [13]:
!pip install sentencepiece

     |████████████████████████████████| 1.2 MB 5.3 MB/s 


Loading pretrained XLM Roberta tokenizer and Encoder

In [14]:
from transformers import AutoTokenizer, TFAutoModel, TFXLMRobertaModel

bert_tokenizer = AutoTokenizer.from_pretrained('jplu/tf-xlm-roberta-base')
# bert_model = TFAutoModel.from_pretrained("jplu/tf-xlm-roberta-large")
bert_model = TFXLMRobertaModel.from_pretrained('jplu/tf-xlm-roberta-base')

Downloading:   0%|          | 0.00/512 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/4.83M [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/1.76G [00:00<?, ?B/s]

Some layers from the model checkpoint at jplu/tf-xlm-roberta-base were not used when initializing TFXLMRobertaModel: ['lm_head']
- This IS expected if you are initializing TFXLMRobertaModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing TFXLMRobertaModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
All the layers of TFXLMRobertaModel were initialized from the model checkpoint at jplu/tf-xlm-roberta-base.
If your task is similar to the task the model of the checkpoint was trained on, you can already use TFXLMRobertaModel for predictions without further training.


Tokenize text

In [15]:
# Tokenize the input (takes some time) 
# here tokenizer using from bert-base-cased
x_train = bert_tokenizer(
    text=X_train,
    add_special_tokens=True,
    max_length=512,
    truncation=True,
    padding=True, 
    return_tensors='tf',
    return_token_type_ids = False,
    return_attention_mask = True,
    verbose = True)
x_test = bert_tokenizer(
    text=X_test,
    add_special_tokens=True,
    max_length=512,
    truncation=True,
    padding=True, 
    return_tensors='tf',
    return_token_type_ids = False,
    return_attention_mask = True,
    verbose = True)

One hot encode of class (y)

In [16]:
from sklearn.preprocessing import LabelEncoder
from sklearn.preprocessing import OneHotEncoder
def make_ohe(y_label):
  # Label Encode
  encoder = LabelEncoder()
  class_labels = encoder.fit_transform(y_label)
  print(class_labels,len(class_labels),class_labels.shape)
  print(set(class_labels))

  #One hot Encode
  encoder = OneHotEncoder(sparse=False)
  class_labels = class_labels.reshape((class_labels.shape[0], 1))
  y_ohe = encoder.fit_transform(class_labels)
  print(y_ohe,y_ohe.shape)
  return y_ohe

In [17]:
y_train = make_ohe(y_train)
print(type(y_train))
y_test = make_ohe(y_test)
print(type(y_test))

[1 1 0 ... 0 0 0] 1500 (1500,)
{0, 1}
[[0. 1.]
 [0. 1.]
 [1. 0.]
 ...
 [1. 0.]
 [1. 0.]
 [1. 0.]] (1500, 2)
<class 'numpy.ndarray'>
[1 0 0 0 0 0 1 0 0 1 0 1 0 0 0 1 0 0 0 1 1 1 1 0 0 0 0 0 1 1 1 1 0 0 0 1 1
 1 0 0 1 0 0 1 1 1 0 1 1 1 0 1 0 1 0 0 0 0 1 1 1 0 0 0 1 1 1 0 1 0 1 0 1 0
 1 1 0 0 0 1 1 0 1 0 0 1 0 1 0 0 1 1 0 1 0 1 1 1 1 1 0 1 1 0 0 0 0 1 1 1 0
 1 1 0 0 0 1 1 0 1 0 1 1 1 0 1 0 0 1 0 1 0 0 1 0 1 1 1 1 1 0 0 0 1 0 1 1 1
 0 1 0 0 1 0 0 0 0 1 0 0 0 1 1 0 0 0 1 1 0 1 0 0 0 0 1 1 0 0 1 1 0 0 1 0 1
 0 0 0 1 0 1 0 1 1 1 1 0 0 0 0 1 0 1 1 0 1 1 0 1 0 1 1 0 0 1 0 0 1 0 0 1 1
 1 1 1 1 0 0 0 1 1 0 0 1 0 0 0 0 0 0 0 1 1 1 0 1 1 0 1 0 1 1 1 0 1 1 0 1 1
 0 0 1 0 0 1 0 0 0 1 0 0 1 1 0 1 1 0 0 0 0 1 0 0 1 0 0 0 1 1 0 0 0 0 1 0 0
 1 0 1 0 0 0 0 1 1 1 0 0 1 1 0 1 1 0 0 0 0 1 0 0 0 0 0 1 0 0 0 0 1 1 0 0 0
 0 1 0 1 1 0 1 0 0 1 0 0 1 0 0 1 1 1 0 1 1 0 0 0 0 1 1 1 1 1 1 0 1 1 1 1 1
 0 1 1 0 1 0 1 1 1 1 0 0 1 1 1 1 1 0 0 1 1 0 0 1 0 0 0 0 0 1 0 1 0 0 0 1 1
 1 0 0 0 0 0 0 0 0 1 1 1 0 0 0 0 1 1 1 0 1 

Classifier model Using XLMRoberta encoder and dense layer

In [18]:
max_len = 512
input_ids = Input(shape=(max_len,), dtype=tf.int32, name="input_ids")
input_mask = Input(shape=(max_len,), dtype=tf.int32, name="attention_mask")
embeddings = bert_model(input_ids,attention_mask = input_mask)[0]
print(np.shape(embeddings))
out = tf.keras.layers.GlobalMaxPool1D()(embeddings)
# out = Dense(128, activation='relu')(out)
# out = tf.keras.layers.Dropout(0.1)(out)
out = Dense(32,activation = 'relu')(out)
y = Dense(2, activation='sigmoid')(out)
model = tf.keras.Model(inputs=[input_ids, input_mask], outputs=y)
model.layers[2].trainable = True
model.summary()

(None, 512, 768)
Model: "model"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 input_ids (InputLayer)         [(None, 512)]        0           []                               
                                                                                                  
 attention_mask (InputLayer)    [(None, 512)]        0           []                               
                                                                                                  
 tfxlm_roberta_model (TFXLMRobe  TFBaseModelOutputWi  278043648  ['input_ids[0][0]',              
 rtaModel)                      thPoolingAndCrossAt               'attention_mask[0][0]']         
                                tentions(last_hidde                                               
                                n_state=(None, 512,                          

In [19]:
optimizer = Adam(
    learning_rate=5e-05, # this learning rate is for bert model , taken from huggingface website 
    epsilon=1e-08,
    decay=0.01,
    clipnorm=1.0)
# Set loss and metrics
# loss =CategoricalCrossentropy(from_logits = True)
# metrics = CategoricalAccuracy('balanced_accuracy'),
loss='binary_crossentropy'
metrics=['accuracy']
# Compile the model
model.compile(
    optimizer = optimizer,
    loss = loss, 
    metrics = metrics)

training model & saving checkpoint

In [ ]:
checkpoint_filepath = 'checkpoint_bert_base_2k_2'
model_checkpoint_callback = tf.keras.callbacks.ModelCheckpoint(
    filepath=checkpoint_filepath,
    save_weights_only=True,
    monitor='val_accuracy',
    mode='max',
    save_best_only=True)
early_stop = tf.keras.callbacks.EarlyStopping(monitor='val_loss', patience=2, restore_best_weights=True)
train_history = model.fit(x ={'input_ids':x_train['input_ids'],'attention_mask':x_train['attention_mask']},y= y_train, epochs=2, validation_split=0.1, batch_size=6, shuffle=True, callbacks=[early_stop, model_checkpoint_callback])

Epoch 1/2
225/225 [==============================] - 10699s 47s/step - loss: 0.0038 - accuracy: 0.9993 - val_loss: 0.0310 - val_accuracy: 0.9933
Epoch 2/2
174/225 [======================>.......] - ETA: 44:18 - loss: 0.0077 - accuracy: 0.9990

Loading saved weights after 1 epoch

In [21]:
model.load_weights('checkpoint_bert_base_2k_2')

Retraining the saved model for another epoch ( It started to ran for 2nd time so i stopped it interrupting)

In [24]:
checkpoint_filepath = 'checkpoint_bert_base_2k_2'
model_checkpoint_callback = tf.keras.callbacks.ModelCheckpoint(
    filepath=checkpoint_filepath,
    save_weights_only=True,
    monitor='val_accuracy',
    mode='max',
    save_best_only=True)
early_stop = tf.keras.callbacks.EarlyStopping(monitor='val_loss', patience=2, restore_best_weights=True)
train_history = model.fit(x ={'input_ids':x_train['input_ids'],'attention_mask':x_train['attention_mask']},y= y_train, epochs=1, validation_split=0.1, batch_size=6, shuffle=True, callbacks=[early_stop])

  1/225 [..............................] - ETA: 5:57:13 - loss: 4.4309e-04 - accuracy: 1.0000

KeyboardInterrupt: ignored

Saved the model after 2 epoch

In [23]:
model.save("bert_xlmroberta_2k_2.h5")

Evaluation of the model on train and test set

In [25]:
from sklearn.metrics import classification_report

# Predict Train set result
predicted_raw_train = model.predict({'input_ids':x_train['input_ids'],'attention_mask':x_train['attention_mask']})
y_predicted_train = np.argmax(predicted_raw_train, axis = 1)
y_true_train = np.argmax(y_train, axis = 1)
print(classification_report(y_true_train, y_predicted_train))

#Predict test set result
predicted_raw = model.predict({'input_ids':x_test['input_ids'],'attention_mask':x_test['attention_mask']})
y_predicted = np.argmax(predicted_raw, axis = 1)
y_true = np.argmax(y_test, axis = 1)
print(classification_report(y_true, y_predicted))


              precision    recall  f1-score   support

           0       1.00      1.00      1.00       781
           1       1.00      1.00      1.00       719

    accuracy                           1.00      1500
   macro avg       1.00      1.00      1.00      1500
weighted avg       1.00      1.00      1.00      1500

              precision    recall  f1-score   support

           0       1.00      1.00      1.00       260
           1       1.00      1.00      1.00       240

    accuracy                           1.00       500
   macro avg       1.00      1.00      1.00       500
weighted avg       1.00      1.00      1.00       500



**Write up:**
1. Link to hugging face model:
https://huggingface.co/Sajib-006/fake_news_detection_xlmRoberta
2. As we can see, there is almost 100% accuracy and F1-score for 2000 dataset, so i haven't tried to find misclassified data.
3. I couldn't run the model for the whole dataset as i used google colab free version, there was RAM and disk restrictions. XLMRoberta is a heavy model, so training it for the full dataset tends to tke huge time. Colab doesn't provide GPU for long time. 
4. As one run for one epoch took huge time, i had to save checkpoint after 1 epoch and retrain the model loading weights for 2nd time. After 2 epoch it showed almost 100% accuracy, so i didn't continue to train again.
5. A more clear picture could have been seen if it could be run for the full dataset. I thought of some ideas about better model but couldn't implement for hardware restriction as mentioned and time constraint. My ideas are-


    *   Adding dense layer and dropout layer to reduce overfitting(Though in my result there is 100% accuracy on hold-out test set, so no overfitting seems to be there)
    *   Adding convolutional layer after the bert encoder work even better.
    *   Combination of different complex convolution layers can be added to check if accuracy increases further more.
    *   Hyperparameter tuning of the layers to ensure best result.



In [ ]:
### WRITE YOUR CODE TO TRAIN THE MODEL HERE

**Write up**: 
* Link to the model on Hugging Face Hub: 
* Include some examples of misclassified news articles. Please explain what you might do to improve your model's performance on these news articles in the future (you do not need to impelement these suggestions)

# 3. Deep RL / Robotics

**RL for Classical Control:** Using any of the [classical control](https://github.com/openai/gym/blob/master/docs/environments.md#classic-control) environments from OpenAI's `gym`, implement a deep NN that learns an optimal policy which maximizes the reward of the environment.

* Describe the NN you implemented and the behavior you observe from the agent as the model converges (or diverges).
* Plot the reward as a function of steps (or Epochs).
Compare your results to a random agent.
* Discuss whether you think your model has learned the optimal policy and potential methods for improving it and/or where it might fail.
* (Optional) [Upload the the model to the Hugging Face Hub](https://huggingface.co/docs/hub/adding-a-model), and add a link to your model below.


You may use any frameworks you like, but you must implement your NN on your own (no pre-defined/trained models like [`stable_baselines`](https://stable-baselines.readthedocs.io/en/master/)).

You may use any simulator other than `gym` _however_:
* The environment has to be similar to the classical control environments (or more complex like [`robosuite`](https://github.com/ARISE-Initiative/robosuite)).
* You cannot choose a game/Atari/text based environment. The purpose of this challenge is to demonstrate an understanding of basic kinematic/dynamic systems.

In [ ]:
### WRITE YOUR CODE TO TRAIN THE MODEL HERE

**Write up**: 
* (Optional) link to the model on Hugging Face Hub: 
* Discuss whether you think your model has learned the optimal policy and potential methods for improving it and/or where it might fail.

# 4. Theory / Linear Algebra 

**Implement Contrastive PCA** Read [this paper](https://www.nature.com/articles/s41467-018-04608-8) and implement contrastive PCA in Python.

* First, please discuss what kind of dataset this would make sense to use this method on
* Implement the method in Python (do not use previous implementations of the method if they already exist)
* Then create a synthetic dataset and apply the method to the synthetic data. Compare with standard PCA.


**Write up**: Discuss what kind of dataset it would make sense to use Contrastive PCA

In [ ]:
### WRITE YOUR CODE HERE

# 5. Systems

**Inference on the edge**: Measure the inference times in various computationally-constrained settings

* Pick a few different speech detection models (we suggest looking at models  on the [Hugging Face Hub](https://huggingface.co/models?pipeline_tag=automatic-speech-recognition&sort=downloads))
* Simulate different memory constraints and CPU allocations that are realistic for edge devices that might run such models, such as smart speakers or microcontrollers, and measure what is the average inference time of the models under these conditions 
* How does the inference time vary with (1) choice of model (2) available system memory (3) available CPU (4) size of input?

Are there any surprising discoveries? (Note that this coding challenge is fairly open-ended, so we will be considering the amount of effort invested in discovering something interesting here).

In [ ]:
### WRITE YOUR CODE HERE

**Write up**: What surprising discoveries do you see?